# Pretrain shift

Now we need to load the n=2 model, then pretrain more serially. 

In [1]:
import torch
import torch.nn as nn

# Needed for parallel 
from collections import OrderedDict
import copy

# For training 
from network_architecture_v2 import MyBertForSequenceClassification

# For fine tuning
from datasets import load_dataset #, load_metric
from transformers import BertTokenizer, BertTokenizerFast, DataCollatorForLanguageModeling
from transformers import Trainer, TrainingArguments
import numpy as np

# Training stuff
from transformers import get_linear_schedule_with_warmup
from torch.utils.data import DataLoader
from datasets import load_dataset
from tqdm.notebook import tqdm

from timeit import default_timer as timer
import time

# Need to now also get the optimizer 
import torch.optim as optim

# Load the parallel model and optimizer

There's an error somewhere with the loading of the optimizer checkpoint for some reason. This is not debugged yet, but needs to be discussed with someone since I couldn't debug it. In the meantime, I load the serial case. 


Two ways: 
1. From notebook - take n=2 parallelnet -> serialnet
2. Take n=2 parallelnet, n=2 parallelnet 1 level (slower)

In [2]:
checkpoint_0 = torch.load('bert-save-2/model_checkpoint_0_batch_idx=30000')
checkpoint_1 = torch.load('bert-save-2/model_checkpoint_1_batch_idx=30000')
checkpoint_serial = torch.load('bert-save-1/model_serial_checkpoint_batch_idx=30000')

In [3]:
keys_0 = checkpoint_0['model_state_dict'].keys()
keys_1 = checkpoint_1['model_state_dict'].keys()

In [4]:
# Just sort of combine everything togeter
optimizer_new_dict = dict()

# First deal with the easy stuff; deep copy is important since objects in list is issues
new_param_groups = copy.deepcopy(checkpoint_0['optimizer_state_dict']['param_groups'])
new_param_groups[0]['params'] = list(
    range(
            new_param_groups[0]['params'][-1] + 2  +  
            checkpoint_1['optimizer_state_dict']['param_groups'][0]['params'][-1]
         )
)
# print(new_param_groups[0]['params'])

# Now deal with the steps
new_state = dict()
for key in checkpoint_0['optimizer_state_dict']['state'].keys():
    new_state[key] = copy.deepcopy(checkpoint_0['optimizer_state_dict']['state'][key])
    # print(
    #     checkpoint_serial['optimizer_state_dict']['state'][key]['exp_avg'].shape,
    #     new_state[key]['exp_avg'].shape
    # )
key += 1
new_state[key] = {'exp_avg': torch.zeros((30522)), 'exp_avg_sq': torch.zeros((30522)), 'step': copy.deepcopy(new_state[key-1]['step'])}

# print(new_state[key-1]['exp_avg_sq'].shape)
# print(new_state[key-1]['exp_avg'].shape)

# This is really annoying, but it's missing a key here... 
shift = key 
for key in checkpoint_1['optimizer_state_dict']['state'].keys():
    new_state[shift + key + 1] = copy.deepcopy(checkpoint_1['optimizer_state_dict']['state'][key])

optimizer_new_dict['param_groups'] = new_param_groups
optimizer_new_dict['state'] = new_state
# print(new_param_groups)
# print(new_state.keys())

In [5]:
# Ugh, this is 
new_dict = OrderedDict()
keys_0 = checkpoint_0['model_state_dict'].keys()
counter = 0
other_counter = 0
for key in keys_0:
    if 'parallel_nn' in key:
        split = key.split('.')
        split[1] = 'serial_nn'
        if int(split[2]) > counter:
            counter = int(split[2])
            
        split.insert(3, 'layer')
        new_key = '.'.join(split[1:])
        new_dict[new_key] = checkpoint_0['model_state_dict'][key]
    else:
        new_key = key
        if 'close_nsp' in key:
            # print(key)
            split = key.split('.')
            split[0] = 'close_nn_nsp'
            new_key = '.'.join(split)
        if 'close_mlm' in key:
            # print(key)
            split = key.split('.')
            split[0] = 'close_nn_mlm'
            new_key = '.'.join(split)
        
        new_dict[new_key] = checkpoint_0['model_state_dict'][key]
    if len(new_dict[new_key].shape) > 0:
        # print(other_counter, new_dict[new_key].shape, optimizer_new_dict['state'][other_counter]['exp_avg'].shape)
        # print(
        #     checkpoint_0['optimizer_state_dict']['state'][other_counter]['exp_avg'].shape
        # )
        other_counter += 1
print(other_counter)
print(counter)

# other_counter = 0
# Now for the remaining parts? 
keys_1 = checkpoint_1['model_state_dict'].keys()
for key in keys_1:
    if 'parallel_nn' in key:
        split = key.split('.')
        split[1] = 'serial_nn'
        split[2] = str(int(split[2]) + counter + 1)
        split.insert(3, 'layer')
        
        new_key = '.'.join(split[1:])
        new_dict[new_key] = checkpoint_1['model_state_dict'][key]
    else:
        new_dict[key] = checkpoint_1['model_state_dict'][key]
    if len(new_dict[new_key].shape) > 0:
        # print(other_counter, new_dict[new_key].shape, optimizer_new_dict['state'][other_counter]['exp_avg'].shape)
        other_counter += 1
print(other_counter)
 

284
16
524


In [6]:
model_parallel = torch.load('serialnet_bert_32')
model_parallel.load_state_dict(new_dict)

<All keys matched successfully>

# Load optimizer and scheduler 

In [7]:
weight_decay=0.01
betas=(0.9, 0.98)

optimizer = optim.AdamW(
    model_parallel.parameters(), lr=5e-5, betas=betas, 
    weight_decay=weight_decay, eps=1e-6
)

optim_schedule = get_linear_schedule_with_warmup(
    optimizer,
    num_warmup_steps=10000,     # Number of warmup steps # TODO: make sure this is correct
    num_training_steps=100000   # Total number of training steps
)


In [8]:
optim_schedule.load_state_dict(
    checkpoint_0['scheduler_state_dict']
)

In [15]:
# optimizer.load_state_dict(checkpoint_serial['optimizer_state_dict'])

# Now load data and train? 

In [18]:
batch_size = 256
sequence_length = 64

In [19]:
# Load C4 Dataset
print('Loading dataset')
dataset = load_dataset("allenai/c4", "en", split="train", streaming=True)
dataset = dataset.remove_columns(['timestamp', 'url'])

Loading dataset


Resolving data files:   0%|          | 0/1024 [00:00<?, ?it/s]

Resolving data files:   0%|          | 0/1024 [00:00<?, ?it/s]

In [20]:
# dataset = dataset.shuffle(42, buffer_size=1_000_000)

In [21]:
# Load tokenizer
tokenizer = BertTokenizerFast.from_pretrained("bert-base-uncased")
vocab_size = tokenizer.vocab_size

# Tokenize the dataset
def tokenize_function(examples):
  return tokenizer(examples["text"], truncation=True, padding="max_length", max_length=sequence_length)

tokenized_dataset = dataset.map(tokenize_function, batched=True, remove_columns=["text"])
tokenized_dataset = tokenized_dataset.with_format("torch")

# Collator; can do MLM with higher prob
data_collator = DataCollatorForLanguageModeling(tokenizer=tokenizer, mlm=True, mlm_probability=0.20) # Doing higher 
train_loader = DataLoader(
 tokenized_dataset, batch_size=batch_size, 
    collate_fn=data_collator, 
    pin_memory=True, drop_last=True
)

In [22]:
# This is the dumbest way to do this, but go a bit into the dataloader; it seems to be random so no need to go far
for batch_idx, batch in tqdm(enumerate(train_loader)):
    if batch_idx == 1000:
        break
        

0it [00:00, ?it/s]

You're using a BertTokenizerFast tokenizer. Please note that with a fast tokenizer, using the `__call__` method is faster than using a method to encode the text followed by a call to the `pad` method to get a padded encoding.


# Now go train 

In [23]:
def train(model, train_loader, optimizer, epoch, device, scheduler):
    train_times = []
    fwd_times = []
    bwd_times = []
    losses = []
    
    # Train the model
    model.train()
    
    criterion = nn.CrossEntropyLoss(ignore_index=-100)
    
    total_time = 0.0
    with open(f'training_log_epoch.out', 'w') as f:    
        for batch_idx, batch_data in enumerate(train_loader):
            optimizer.zero_grad()
            
            data, target, segment_label = batch_data['input_ids'], batch_data['labels'], batch_data['token_type_ids']
            
            start_time = timer()
            data, target, segment_label = data.to(device), target.to(device), segment_label.to(device)
            
            torch.cuda.synchronize()
            batch_fwd_pass_start = time.time()
            mask_lm_output = model(data, segment_label)
            torch.cuda.synchronize()
            batch_fwd_pass_end = time.time()
            
            mask_loss = criterion(mask_lm_output.reshape(-1, mask_lm_output.shape[-1]), target.reshape(-1))
            
            loss = mask_loss
            
            torch.cuda.synchronize()
            batch_bwd_pass_start = time.time()
            loss.backward()
            torch.cuda.synchronize()
            batch_bwd_pass_end = time.time()
            optimizer.step()
            scheduler.step()  # Update the learning rate
            
            stop_time = timer()
            
            total_time += stop_time - start_time
            train_times.append(stop_time - start_time)
            fwd_times.append(batch_fwd_pass_end - batch_fwd_pass_start)
            bwd_times.append(batch_bwd_pass_end - batch_bwd_pass_start)
            losses.append(loss.item())
            
            # Generate new dropout mask 
            model.new_mask()
            
            if batch_idx % 1000 == 0:
                checkpoint = {
                  'model_state_dict': model.state_dict(),
                  'optimizer_state_dict': optimizer.state_dict(),
                  'scheduler_state_dict': scheduler.state_dict()
                }
                torch.save(checkpoint, f'bert-save-extend/model_serial_checkpoint_{batch_idx=}')
            
            if batch_idx % 1 == 0:
                print(f'Train Epoch: {epoch} {batch_idx} {loss.item()} {scheduler.get_last_lr()}', file=f, flush=True)
                print(f'\t Some times: {fwd_times[-4:-1]=} {bwd_times[-4:-1]=} {train_times[-4:-1]=}', file=f,flush=True)
                print(f'Train Epoch: {epoch} {batch_idx} {loss.item()} {scheduler.get_last_lr()}')
                print(f'\t Some times: {fwd_times[-4:-1]=} {bwd_times[-4:-1]=} {train_times[-4:-1]=}')

            if batch_idx == 80000:
                break
            
    return losses, train_times, fwd_times, bwd_times

In [ ]:
[losses, train_times, batch_f_times, batch_b_times] = train(model=model_parallel, train_loader=train_loader, optimizer=optimizer, epoch=1,
      device='cuda', scheduler=optim_schedule)


Train Epoch: 1 0 4.562469482421875 [3.888777777777778e-05]
	 Some times: fwd_times[-4:-1]=[] bwd_times[-4:-1]=[] train_times[-4:-1]=[]
Train Epoch: 1 1 4.4900994300842285 [3.888722222222223e-05]
	 Some times: fwd_times[-4:-1]=[1.1835870742797852] bwd_times[-4:-1]=[1.0828795433044434] train_times[-4:-1]=[2.3029952868819237]
Train Epoch: 1 2 4.567676544189453 [3.888666666666667e-05]
	 Some times: fwd_times[-4:-1]=[1.1835870742797852, 0.5290617942810059] bwd_times[-4:-1]=[1.0828795433044434, 1.0807628631591797] train_times[-4:-1]=[2.3029952868819237, 1.6238387804478407]
Train Epoch: 1 3 4.488958835601807 [3.888611111111111e-05]
	 Some times: fwd_times[-4:-1]=[1.1835870742797852, 0.5290617942810059, 0.5296323299407959] bwd_times[-4:-1]=[1.0828795433044434, 1.0807628631591797, 1.0779616832733154] train_times[-4:-1]=[2.3029952868819237, 1.6238387804478407, 1.6208912935107946]
Train Epoch: 1 4 4.443748474121094 [3.888555555555556e-05]
	 Some times: fwd_times[-4:-1]=[0.5290617942810059, 0.5296